In [1]:
import torch
from requests import request
from requests.compat import *
from bs4 import BeautifulSoup
import pandas as pd
import math
import time
import os
import requests

def makePageDF(category_id, page_id, pagingsize):

    max_attempts = 3  # Maximum number of attempts to fetch data from a page
    attempts = 0

    while attempts < max_attempts:
        try:
            url = 'https://search.shopping.naver.com/search/category/' + str(category_id)
            params = {
                'pagingIndex' : str(page_id),
                'pagingSize' : str(pagingsize),
                'productSet' : 'model'
            }
            headers = {'User-Agent': 'Yeti',}
            resp = request('GET',url=url, params=params, headers=headers)
            print(resp.request.url)
            dom = BeautifulSoup(resp.text, 'html.parser')
            script_tag = dom.find("script", {"id": "__NEXT_DATA__"})

            if script_tag:
                data = json.loads(script_tag.text)
                itemList = data['props']['pageProps']['initialState']['products']


                # 각 상품의 정보를 저장할 리스트를 생성합니다.
                products_info = []

                for item in itemList['list'][:pagingsize]:

                    attributes_dict = dict()
                    # 'attributeValue'와 'characterValue' 문자열을 리스트로 분리합니다.
                    attribute_values = item['item'].get('attributeValue','').split('|')
                    character_values = item['item'].get('characterValue','').split('|')

                    # 'attributeValue' 리스트의 각 요소에서 '_M' 문자열을 제거합니다.
                    attribute_values = [value.replace('_M', '') for value in attribute_values]

                    min_len = min(len(attribute_values), len(character_values))

                    for j in range(min_len):
                        attribute = attribute_values[j]
                        character = character_values[j]

                        if attribute in attributes_dict:
                            attributes_dict[attribute].append(character)
                        else:
                            attributes_dict[attribute] = [character]

                    attribute_list = [item['item']['category3Name']]

                    for i in attributes_dict:
                        if i not in ['용량', '구성', '']:
                            attribute_list = attribute_list + attributes_dict[i]
                        else:
                            continue

                    dict_data = {
                        'ID': item['item']['id'],
                        '상품명': item['item']['productName'],
                        '상품 카테고리 대분류': item['item']['category1Name'],
                        '상품 카테고리 중분류': item['item']['category2Name'],
                        '상품 카테고리 소분류': item['item']['category3Name'],
                        '제조사': item['item'].get('maker',''),
                        '브랜드': item['item'].get('brand',''),
                        '특징': attribute_list,
                        '느낌': item['item'].get('atmtTag','').replace('|',',').split(','),
                        '평점': item['item'].get('scoreInfo',0),
                    }

                    products_info.append(dict_data)

                total = data['props']['pageProps']['initialState']['products']['total']
                total_page = math.ceil(total/int(params['pagingSize']))

                    # 딕셔너리의 리스트를 데이터프레임으로 변환합니다.
                df = pd.DataFrame(products_info)

                return df,total_page
            else:
                attempts += 1
                print("script_tag not found on page", page_id)
                time.sleep(1)  # Wait for a short time before retrying
        except requests.exceptions.RequestException as e:
            attempts += 1
            print("Request Exception:", e)
            time.sleep(1)  # Wait for a short time before retrying
        except (ValueError, KeyError, AttributeError, TypeError) as e:
            attempts += 1
            print("Error while processing data:", e)
            time.sleep(1)  # Wait for a short time before retrying

    print(f"Failed to fetch data for page {page_id} after {max_attempts} attempts.")
    return None, None

In [2]:
def CrawlCategoryId(category_id, filename='categoryId.csv'):
    url = 'https://search.shopping.naver.com/search/category/'
    headers = {'User-Agent': 'Yeti',}
    params = {
        'pagingIndex' : '1',
        'pagingSize' : '80',
        'productSet' : 'model'
    }
    resp = request('GET',url=url+str(category_id), headers=headers)
    print(resp.request.url)

    dom = BeautifulSoup(resp.text, 'html.parser')
    script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
    data = json.loads(script_tag.text)

    title_value_pairs = [{'title': x['title'], 'value': x['value']} for x in data['props']['pageProps']['initialState']['mainFilters'][0]['filterValues']]
    category_df = pd.DataFrame(title_value_pairs)

    rows_to_drop = []
    rows_to_append = []

    for index, row in category_df.iterrows():
        category_url = url + str(row['value'])
        time.sleep(0.3)
        resp = request('GET',url=category_url,params=params, headers=headers)
        print(resp.request.url)
        dom = BeautifulSoup(resp.text, 'html.parser')
        script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
        data = json.loads(script_tag.text)

        if data['props']['pageProps']['initialState']['subFilters']:
            product_count = data['props']['pageProps']['initialState']['subFilters'][0]['filterValues'][1]['productCount']
        else:
            product_count = 0

        if int(product_count)/int(params['pagingSize']) > 100:
            print(row['title'], row['value'], product_count, product_count/int(params['pagingSize']))
            rows_to_drop.append(index)
            sub_title_value_pairs = [{'title': x['title'], 'value': x['value']} for x in data['props']['pageProps']['initialState']['mainFilters'][0]['filterValues']]
            rows_to_append += sub_title_value_pairs

    # Drop the rows from original DataFrame
    category_df = category_df.drop(rows_to_drop)

    # Append new rows to DataFrame
    category_df = category_df.append(rows_to_append, ignore_index=True)

    category_df.to_csv(filename, index=False, encoding='utf-8-sig')

    return list(category_df['value'])

In [3]:
def makeCategoryDF(category_id):

    category_id_list = CrawlCategoryId(category_id)
    dfs = []  # 데이터프레임을 저장할 리스트를 생성합니다.

    for j in [60,80]:
        for k in category_id_list:
            new_df,total_page = makePageDF(k,1,j)
            dfs.append(new_df)  # 데이터프레임을 리스트에 추가합니다.
            if total_page > 1:
                for i in range(2,total_page+1):
                    new_df, _ = makePageDF(k,i,j)
                    time.sleep(0.3)
                    dfs.append(new_df)  # 데이터프레임을 리스트에 추가합니다.
            else:
                continue

    # 중복이 제거된 데이터프레임을 다시 불러와서 하나의 데이터프레임으로 합칩니다.
    df = pd.concat(dfs, ignore_index=True)

    df = df.drop_duplicates(subset=['ID'])
    df = df.drop_duplicates(subset=['상품명','제조사'])
    df = df.drop_duplicates(subset=['상품명','브랜드'], ignore_index=True)

    df = pd.DataFrame(df).astype({'제조사': 'category'})
    df = pd.DataFrame(df).astype({'브랜드': 'category'})

    return df

In [6]:
def add_attribute(df,name):
    if name == '성분':
        ingredients_list = []
        for item in df['ID']:
            try:
                url = 'https://search.shopping.naver.com/catalog/' + str(item)
                headers = {'User-Agent': 'Yeti',}
                resp = request('GET',url=url,headers=headers)
                print(resp.request.url)
                dom = BeautifulSoup(resp.text, 'html.parser')
                script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
                data = json.loads(script_tag.text)

                ingredients = data['props']['pageProps']['initialState']['catalog']['cosmeticIngredient'].get('allIngredients','')
                if ingredients:
                    ingredients = ingredients.replace(' ','').split(',')
                ingredients_list.append(ingredients)
                time.sleep(0.5)

            except requests.exceptions.RequestException as e:
                print("Request Exception:", e)
                print("Retrying for item:", item)
                ingredients = []
                ingredients_list.append(ingredients)
                continue

            except (ValueError, KeyError, AttributeError) as e:
                print("Error while processing data:", e)
                print("Retrying for item:", item)
                ingredients = []
                ingredients_list.append(ingredients)
                continue

        df[name] = ingredients_list

    elif name == '네이버 추천 상품 ID':
        recommend_item_id_list = []
        for item in df['ID']:
            try:
                url = 'https://search.shopping.naver.com/catalog/' + str(item)
                headers = {'User-Agent': 'Yeti',}
                resp = request('GET',url=url,headers=headers)
                print(resp.request.url)
                dom = BeautifulSoup(resp.text, 'html.parser')
                script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
                data = json.loads(script_tag.text)
                recommend_item = data['props']['pageProps']['initialState']['catalog']['recommend']['explore']['recItems']
                recommend_item_id = []
                for i in range(len(recommend_item)):
                    if recommend_item[i]['nPayMblType'] == '0':
                        recommend_item_id.append(recommend_item[i]['nvMid'])
                    else:
                        continue
                recommend_item_id_list.append(recommend_item_id)
                time.sleep(0.5)

            except requests.exceptions.RequestException as e:
                print("Request Exception:", e)
                print("Retrying for item:", item)
                recommend_item_id = []
                ingredients_list.append(recommend_item_id)
                continue

            except (ValueError, KeyError, AttributeError) as e:
                print("Error while processing data:", e)
                print("Retrying for item:", item)
                recommend_item_id = []
                ingredients_list.append(recommend_item_id)
                continue

        df[name] = recommend_item_id_list

In [5]:
df = makeCategoryDF(100000003)

https://search.shopping.naver.com/search/category/100000003
https://search.shopping.naver.com/search/category/100008810?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100000926?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100000913?pagingIndex=1&pagingSize=80&productSet=model
스킨케어 100000913 34838 435.475
https://search.shopping.naver.com/search/category/100000920?pagingIndex=1&pagingSize=80&productSet=model
바디케어 100000920 23107 288.8375
https://search.shopping.naver.com/search/category/100000921?pagingIndex=1&pagingSize=80&productSet=model
헤어케어 100000921 15798 197.475
https://search.shopping.naver.com/search/category/100000923?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100001000?pagingIndex=1&pagingSize=80&productSet=model
https://search.shopping.naver.com/search/category/100000915?pagingIndex=1&pagingSize=80&productSet=model
클렌징 10000091

<ipython-input-2-c88c132c2a81>:46: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  category_df = category_df.append(rows_to_append, ignore_index=True)


https://search.shopping.naver.com/search/category/100008810?pagingIndex=1&pagingSize=60&productSet=model
https://search.shopping.naver.com/search/category/100008810?pagingIndex=2&pagingSize=60&productSet=model
https://search.shopping.naver.com/search/category/100008810?pagingIndex=3&pagingSize=60&productSet=model
https://search.shopping.naver.com/search/category/100008810?pagingIndex=4&pagingSize=60&productSet=model
https://search.shopping.naver.com/search/category/100000926?pagingIndex=1&pagingSize=60&productSet=model
https://search.shopping.naver.com/search/category/100000926?pagingIndex=2&pagingSize=60&productSet=model
https://search.shopping.naver.com/search/category/100000926?pagingIndex=3&pagingSize=60&productSet=model
https://search.shopping.naver.com/search/category/100000926?pagingIndex=4&pagingSize=60&productSet=model
https://search.shopping.naver.com/search/category/100000926?pagingIndex=5&pagingSize=60&productSet=model
https://search.shopping.naver.com/search/category/10000

In [8]:
df = pd.read_excel('beautydata.xlsx')

add_attribute(df,'성분')
df.to_excel('data.xlsx')

https://search.shopping.naver.com/catalog/18900649628
https://search.shopping.naver.com/catalog/14136909413
https://search.shopping.naver.com/catalog/26979565522
https://search.shopping.naver.com/catalog/20448242651
https://search.shopping.naver.com/catalog/41771632625
https://search.shopping.naver.com/catalog/21401106806
https://search.shopping.naver.com/catalog/33057692618
https://search.shopping.naver.com/catalog/41029959621
https://search.shopping.naver.com/catalog/22764265976
https://search.shopping.naver.com/catalog/33294468619
https://search.shopping.naver.com/catalog/31884208618
https://search.shopping.naver.com/catalog/40819420619
https://search.shopping.naver.com/catalog/27983219522
https://search.shopping.naver.com/catalog/33577336620
https://search.shopping.naver.com/catalog/22127515706
https://search.shopping.naver.com/catalog/12288948733
https://search.shopping.naver.com/catalog/24994818522
https://search.shopping.naver.com/catalog/41025711618
https://search.shopping.nave

https://search.shopping.naver.com/catalog/32612751622
https://search.shopping.naver.com/catalog/34252263620
https://search.shopping.naver.com/catalog/31330640618
https://search.shopping.naver.com/catalog/38693341620
https://search.shopping.naver.com/catalog/32421996621
https://search.shopping.naver.com/catalog/38674178618
https://search.shopping.naver.com/catalog/30891946619
https://search.shopping.naver.com/catalog/30874804623
https://search.shopping.naver.com/catalog/33575830619
https://search.shopping.naver.com/catalog/25271407525
https://search.shopping.naver.com/catalog/33192602619
https://search.shopping.naver.com/catalog/18903270966
https://search.shopping.naver.com/catalog/35617169618
https://search.shopping.naver.com/catalog/31313413619
https://search.shopping.naver.com/catalog/38442195618
https://search.shopping.naver.com/catalog/29606980626
https://search.shopping.naver.com/catalog/24313026522
https://search.shopping.naver.com/catalog/25270136529
https://search.shopping.nave

https://search.shopping.naver.com/catalog/34937812619
https://search.shopping.naver.com/catalog/36946496622
https://search.shopping.naver.com/catalog/37988064619
https://search.shopping.naver.com/catalog/29045937589
https://search.shopping.naver.com/catalog/41409667622
https://search.shopping.naver.com/catalog/26008777523
https://search.shopping.naver.com/catalog/30789287618
https://search.shopping.naver.com/catalog/33331858619
https://search.shopping.naver.com/catalog/39854970623
https://search.shopping.naver.com/catalog/36308848618
https://search.shopping.naver.com/catalog/35551038618
https://search.shopping.naver.com/catalog/36947138619
https://search.shopping.naver.com/catalog/31570605620
https://search.shopping.naver.com/catalog/35187205620
https://search.shopping.naver.com/catalog/40862878618
https://search.shopping.naver.com/catalog/41635094619
https://search.shopping.naver.com/catalog/38314330623
https://search.shopping.naver.com/catalog/41640865623
https://search.shopping.nave

https://search.shopping.naver.com/catalog/36217531621
https://search.shopping.naver.com/catalog/37255981622
https://search.shopping.naver.com/catalog/34530155618
https://search.shopping.naver.com/catalog/29312476620
https://search.shopping.naver.com/catalog/35475113620
https://search.shopping.naver.com/catalog/35502315618
https://search.shopping.naver.com/catalog/29736419619
https://search.shopping.naver.com/catalog/38778461624
https://search.shopping.naver.com/catalog/36382955619
https://search.shopping.naver.com/catalog/30945621619
https://search.shopping.naver.com/catalog/24365536522
https://search.shopping.naver.com/catalog/40165299618
https://search.shopping.naver.com/catalog/40617742623
https://search.shopping.naver.com/catalog/37442167619
https://search.shopping.naver.com/catalog/32268559618
https://search.shopping.naver.com/catalog/27595957527
https://search.shopping.naver.com/catalog/37171146621
https://search.shopping.naver.com/catalog/38141821618
https://search.shopping.nave

https://search.shopping.naver.com/catalog/36360018620
https://search.shopping.naver.com/catalog/32163541620
https://search.shopping.naver.com/catalog/33231771618
https://search.shopping.naver.com/catalog/34118991618
https://search.shopping.naver.com/catalog/32164482620
https://search.shopping.naver.com/catalog/32163101622
https://search.shopping.naver.com/catalog/37573980619
https://search.shopping.naver.com/catalog/23935790525
https://search.shopping.naver.com/catalog/23934524522
https://search.shopping.naver.com/catalog/36989090619
https://search.shopping.naver.com/catalog/33231772618
https://search.shopping.naver.com/catalog/31297351620
https://search.shopping.naver.com/catalog/36945389618
https://search.shopping.naver.com/catalog/38692379618
https://search.shopping.naver.com/catalog/35579223620
https://search.shopping.naver.com/catalog/35596590622
https://search.shopping.naver.com/catalog/38692296618
https://search.shopping.naver.com/catalog/23936152522
https://search.shopping.nave

...

https://search.shopping.naver.com/catalog/37075547619
https://search.shopping.naver.com/catalog/35748736619
https://search.shopping.naver.com/catalog/12425778998
https://search.shopping.naver.com/catalog/41816997619
https://search.shopping.naver.com/catalog/21884774154
https://search.shopping.naver.com/catalog/34978862627
https://search.shopping.naver.com/catalog/14268198479
https://search.shopping.naver.com/catalog/41568124620
https://search.shopping.naver.com/catalog/41568081621
https://search.shopping.naver.com/catalog/21722117129
https://search.shopping.naver.com/catalog/36008847619
https://search.shopping.naver.com/catalog/9317694280
https://search.shopping.naver.com/catalog/8132049682
https://search.shopping.naver.com/catalog/25914902523
https://search.shopping.naver.com/catalog/33819727618
https://search.shopping.naver.com/catalog/34272356618
https://search.shopping.naver.com/catalog/32133147618
https://search.shopping.naver.com/catalog/30876136618
https://search.shopping.naver.

https://search.shopping.naver.com/catalog/37077698618
https://search.shopping.naver.com/catalog/23919967524
https://search.shopping.naver.com/catalog/25483284522
https://search.shopping.naver.com/catalog/12419646495
https://search.shopping.naver.com/catalog/28452685563
https://search.shopping.naver.com/catalog/33515679619
https://search.shopping.naver.com/catalog/28679629558
https://search.shopping.naver.com/catalog/28473299554
https://search.shopping.naver.com/catalog/28473329554
https://search.shopping.naver.com/catalog/33287840618
https://search.shopping.naver.com/catalog/30800046619
https://search.shopping.naver.com/catalog/28420559554
https://search.shopping.naver.com/catalog/30700871619
https://search.shopping.naver.com/catalog/21513541075
https://search.shopping.naver.com/catalog/32052931619
https://search.shopping.naver.com/catalog/36046069618
https://search.shopping.naver.com/catalog/36990410622
https://search.shopping.naver.com/catalog/28884292587
https://search.shopping.nave

https://search.shopping.naver.com/catalog/29988935621
https://search.shopping.naver.com/catalog/33864771624
https://search.shopping.naver.com/catalog/33937008623
https://search.shopping.naver.com/catalog/34083644618
https://search.shopping.naver.com/catalog/34137956618
https://search.shopping.naver.com/catalog/30415175618
https://search.shopping.naver.com/catalog/29975107618
https://search.shopping.naver.com/catalog/29895063630
https://search.shopping.naver.com/catalog/34214410618
https://search.shopping.naver.com/catalog/31259411624
https://search.shopping.naver.com/catalog/34430487619
https://search.shopping.naver.com/catalog/29903343620
https://search.shopping.naver.com/catalog/35229164619
https://search.shopping.naver.com/catalog/37795206619
https://search.shopping.naver.com/catalog/37179532619
https://search.shopping.naver.com/catalog/34794530619
https://search.shopping.naver.com/catalog/36723923618
https://search.shopping.naver.com/catalog/37645620625
https://search.shopping.nave

https://search.shopping.naver.com/catalog/35192335619
https://search.shopping.naver.com/catalog/33739694627
https://search.shopping.naver.com/catalog/31220043619
https://search.shopping.naver.com/catalog/36465419619
https://search.shopping.naver.com/catalog/30960091619
https://search.shopping.naver.com/catalog/36084931618
https://search.shopping.naver.com/catalog/36719905619
https://search.shopping.naver.com/catalog/29300441622
https://search.shopping.naver.com/catalog/32456992621
https://search.shopping.naver.com/catalog/32268872618
https://search.shopping.naver.com/catalog/36988391620
https://search.shopping.naver.com/catalog/13744728951
https://search.shopping.naver.com/catalog/27859644525
https://search.shopping.naver.com/catalog/26759632523
https://search.shopping.naver.com/catalog/32860529618
https://search.shopping.naver.com/catalog/33119833618
https://search.shopping.naver.com/catalog/32774453621
https://search.shopping.naver.com/catalog/35111108618
https://search.shopping.nave

https://search.shopping.naver.com/catalog/24918238523
https://search.shopping.naver.com/catalog/37522476618
https://search.shopping.naver.com/catalog/36839867620
https://search.shopping.naver.com/catalog/25883613522
https://search.shopping.naver.com/catalog/21444465656
https://search.shopping.naver.com/catalog/25008040525
https://search.shopping.naver.com/catalog/36383615620
https://search.shopping.naver.com/catalog/26980902523
https://search.shopping.naver.com/catalog/27684180526
https://search.shopping.naver.com/catalog/23802296524
https://search.shopping.naver.com/catalog/26292754522
https://search.shopping.naver.com/catalog/37232706630
https://search.shopping.naver.com/catalog/35622221625
https://search.shopping.naver.com/catalog/36337271619
https://search.shopping.naver.com/catalog/30452991624
https://search.shopping.naver.com/catalog/28091041522
https://search.shopping.naver.com/catalog/29298080628
https://search.shopping.naver.com/catalog/25914762527
https://search.shopping.nave

In [28]:
selected_rows = df[df['ID'].isin([22356322357, 13896935945, 34489418621, 8753052124, 34427735619, 41752283618])]
selected_column = selected_rows['성분']

In [29]:
selected_column

31817     []
31823     []
38152     []
44605     []
92228     []
114502    []
Name: 성분, dtype: object

In [30]:
df[df['ID']==22356322357]['성분']

31817    []
Name: 성분, dtype: object

In [35]:
for i in [22356322357, 13896935945, 34489418621, 8753052124, 34427735619, 41752283618]:
    url = 'https://search.shopping.naver.com/catalog/' + str(i)
    headers = {'User-Agent': 'Yeti',}
    resp = request('GET',url=url,headers=headers)
    print(resp.request.url)
    dom = BeautifulSoup(resp.text, 'html.parser')
    script_tag = dom.find("script", {"id": "__NEXT_DATA__"})
    data = json.loads(script_tag.text)

    ingredients = data['props']['pageProps']['initialState']['catalog']['cosmeticIngredient'].get('allIngredients','')
    if ingredients:
        ingredients = ingredients.replace(' ', '').split(',')
        df_index = df[df['ID'] == i].index[0]
        current_ingredients = df.at[df_index, '성분']
        df.at[df_index, '성분'] = current_ingredients + ingredients
    time.sleep(0.5)

https://search.shopping.naver.com/catalog/22356322357
https://search.shopping.naver.com/catalog/13896935945
https://search.shopping.naver.com/catalog/34489418621
https://search.shopping.naver.com/catalog/8753052124
https://search.shopping.naver.com/catalog/34427735619
https://search.shopping.naver.com/catalog/41752283618


In [36]:
df[df['ID']==22356322357]['성분']

31817    [정제수, 티타늄디옥사이드, 카프릴릭/카프릭트라이글리세라이드, 프로판다이올, 사이클...
Name: 성분, dtype: object

In [37]:
df[df['ID']==13896935945]['성분']

31823    [부틸렌글라이콜디카프릴레이트/디카프레이트, 폴리에칠렌, 디메치콘, 옥투크릴렌, 비닐...
Name: 성분, dtype: object

In [39]:
df.to_excel('data.xlsx')